# Analysis of the robustness of PLIER analyisis with GTEx

In this notebook, we will evaluate the robustness of PLIER modules using GTEx data by conducting the analysis with consistent parameters.

## Settings and paths

In [ ]:
INPUT_PLIER_ROB_PATH = NULL 

## Load libraries and data

In [3]:
library(PLIER)
library(ggplot2)
library(assertthat)

source(here::here('scripts/plier_util.R'))
INPUT_PLIER_ROB_PATH=here::here('output/gtex/robustness')

In [4]:
gtex_rob_model_paths <- list.files(INPUT_PLIER_ROB_PATH, full.names = TRUE, pattern = "\\.rds$")

In [5]:
gtex_rob_model_paths

[1] "/home/msubirana/Documents/pivlab/plier_recount3/output/gtex/robustness/gtex_plier_rob_1.rds" 
 [2] "/home/msubirana/Documents/pivlab/plier_recount3/output/gtex/robustness/gtex_plier_rob_10.rds"
 [3] "/home/msubirana/Documents/pivlab/plier_recount3/output/gtex/robustness/gtex_plier_rob_2.rds" 
 [4] "/home/msubirana/Documents/pivlab/plier_recount3/output/gtex/robustness/gtex_plier_rob_3.rds" 
 [5] "/home/msubirana/Documents/pivlab/plier_recount3/output/gtex/robustness/gtex_plier_rob_4.rds" 
 [6] "/home/msubirana/Documents/pivlab/plier_recount3/output/gtex/robustness/gtex_plier_rob_5.rds" 
 [7] "/home/msubirana/Documents/pivlab/plier_recount3/output/gtex/robustness/gtex_plier_rob_6.rds" 
 [8] "/home/msubirana/Documents/pivlab/plier_recount3/output/gtex/robustness/gtex_plier_rob_7.rds" 
 [9] "/home/msubirana/Documents/pivlab/plier_recount3/output/gtex/robustness/gtex_plier_rob_8.rds" 
[10] "/home/msubirana/Documents/pivlab/plier_recount3/output/gtex/robustness/gtex_plier_rob_9.rds"

In [ ]:
# Assuming gtex_rob_model_paths contains the paths to the .rds files
gtex_models <- lapply(gtex_rob_model_paths, readRDS)

# Initialize lists to store the results of comparisons
lv_correlations <- list() # Store LV correlations
gene_overlap_indices <- list() # Store Jaccard indices for gene overlap
pathway_overlap_indices <- list() # Store Jaccard indices for pathway overlap

# Comparing every model with every other model might be redundant,
# so let's compare each model to the first one as a reference.
reference_model <- gtex_models[[1]]

for (i in 2:length(gtex_models)) {
  current_model <- gtex_models[[i]]
  
  # Compare LVs (B matrices)
  lv_correlations[[i-1]] <- cor(reference_model$B, current_model$B)
  
  # Compare gene associations for the first LV as an example
  top_genes_ref <- order(reference_model$Z[, 1], decreasing = TRUE)[1:10]
  top_genes_current <- order(current_model$Z[, 1], decreasing = TRUE)[1:10]
  gene_overlap_indices[[i-1]] <- jaccard_index(names(top_genes_ref), names(top_genes_current))
  
  # Compare pathway associations for the first LV as an example
  top_pathways_ref <- which(reference_model$U[, 1] != 0)
  top_pathways_current <- which(current_model$U[, 1] != 0)
  pathway_overlap_indices[[i-1]] <- jaccard_index(names(top_pathways_ref), names(top_pathways_current))
}

# Example to calculate average correlation across LVs for the first comparison
average_cor_lv1 <- mean(lv_correlations[[1]], na.rm = TRUE)

# Display average LV correlation for the first comparison
print(average_cor_lv1)

# Display Jaccard index for gene overlap for the first LV comparison
print(gene_overlap_indices[[1]])

# Display Jaccard index for pathway overlap for the first LV comparison
print(pathway_overlap_indices[[1]])


In [18]:
gtex_rob_model_path=gtex_rob_model_paths[1]
gtex_rob_model=readRDS(gtex_rob_model_path)

- **B**: latent variable matrix with dimension k-by-samples. You can correlate this matrix with the phenotype of interest
- **Z**: loading matrix with dimension genes-by-k. You can check which genes are top ranked with respect to each LV by ordering the loading values (decreasing order) in a column-wise manner
- **U**: coefficient matrix with dimension pathways-by-k. This encodes the combination of pathways for each LV
- **C**: The exact pathway matrix used in the decomposition which may be different from the input
- **withPrior** An index vector which indicates the list of LVs that are associated with pathways
- **Up Uauc and Up**: are AUC and p.val matrices with the same dimension as U. They are calculated based on cross-validation to test how reliable pathways are associated with LVs. All entries with non-zero AUC are collected to formulate summary
- **summary**: This is based on Uauc and Up which records pathway-LV pairs that are supported by cross-validation test. For a given LV, if you find the associated pathways are interesting, you may want to double check the top ranked genes for this LV by looking at Z

In [27]:
matrixU <- gtex_rob_model$U
matrixZ <- gtex_rob_model$Z
matrixB <- gtex_rob_model$B
PLIER_summary=gtex_rob_model$summary
gtex_rob_model$L1

In [43]:
head(PLIER_summary)

pathway                 LV index AUC       p-value      FDR         
1 IRIS_Neutrophil-Resting 1        0.5955477 3.089207e-03 9.624810e-03
2 IRIS_Monocyte-Day0      2        0.5655353 5.209197e-02 9.886236e-02
3 IRIS_Neutrophil-Resting 2        0.6826786 5.800617e-09 1.020567e-07
4 DMAP_GRAN2              2        0.6939956 2.765659e-04 1.216483e-03
5 DMAP_GRAN3              2        0.5531333 1.533024e-01 2.343012e-01
6 DMAP_MONO1              2        0.6008004 4.519634e-02 8.818046e-02

In [51]:
head(matrixZ)

[,1]       [,2]       [,3]      [,4]       [,5]      [,6]      
GAS6     0.20762129 0.00000000 0.0000000 0.00000000 0.0000000 0.02653939
MMP14    0.09893808 0.00000000 0.0000000 0.03620340 0.0000000 0.00000000
MARCKSL1 0.00000000 0.00000000 0.0689154 0.00000000 0.0000000 0.06473675
SPARC    0.00000000 0.00000000 0.0000000 0.08840532 0.0000000 0.00000000
CTSD     0.00000000 0.09038044 0.3689761 0.05409820 0.1073371 0.00000000
EPAS1    0.01069210 0.00000000 0.0000000 0.00000000 0.0000000 0.04134291
         [,7]       [,8]       [,9]       [,10]      [,11] [,12]     [,13]     
GAS6     0.00000000 0.00000000 0.62387382 0.18440284 ⋯     0.0000000 0.00000000
MMP14    0.00000000 0.00000000 0.57073574 0.00000000 ⋯     0.0000000 0.02603330
MARCKSL1 0.00000000 0.00000000 0.06586991 0.04277300 ⋯     0.1104464 0.00000000
SPARC    0.00000000 0.03131448 0.20514237 0.45000462 ⋯     0.0000000 0.00000000
CTSD     0.00000000 0.09150932 1.38866053 0.02098779 ⋯     0.0000000 0.02845362
EPAS1    0.03603086 0.00000000 0.11679199 0.11713569 ⋯     0.0000000 0.00000000
         [,14]     [,15]      [,16]      [,17]      [,18] [,19]      [,20]     
GAS6     0.1552670 0.00000000 0.00000000 0.03676118 0     0.03729953 0.01813663
MMP14    0.0000000 0.01795993 0.02515933 0.00000000 0     0.00000000 0.13488302
MARCKSL1 0.0000000 0.00000000 0.00000000 0.00000000 0     0.00000000 0.00000000
SPARC    0.1168224 0.00000000 0.03407571 0.13301524 0     0.01732749 0.00000000
CTSD     0.2228255 0.00000000 0.00000000 0.00000000 0     0.00000000 0.04607547
EPAS1    0.0000000 0.00000000 0.37824176 0.00000000 0     0.00000000 0.28356290
         [,21]     
GAS6     0.32003652
MMP14    0.32878006
MARCKSL1 0.07458389
SPARC    0.00000000
CTSD     0.54812303
EPAS1    0.14947889

In [50]:
head(gtex_rob_model$Uauc)

LV1 LV2 LV3 LV4       LV5 LV6 LV7 LV8 LV9
IRIS_Bcell-Memory_IgG_IgA            0   0   0   0.0000000 0   0   0   0   0  
IRIS_Bcell-Memory_IgM                0   0   0   0.0000000 0   0   0   0   0  
IRIS_Bcell-naive                     0   0   0   0.0000000 0   0   0   0   0  
IRIS_CD4Tcell-N0                     0   0   0   0.0000000 0   0   0   0   0  
IRIS_CD4Tcell-Th1-restimulated12hour 0   0   0   0.0000000 0   0   0   0   0  
IRIS_CD4Tcell-Th1-restimulated48hour 0   0   0   0.9270726 0   0   0   0   0  
                                     LV10 ⋯ LV1033 LV1034 LV1035 LV1036 LV1037
IRIS_Bcell-Memory_IgG_IgA            0    ⋯ 0      0      0      0      0     
IRIS_Bcell-Memory_IgM                0    ⋯ 0      0      0      0      0     
IRIS_Bcell-naive                     0    ⋯ 0      0      0      0      0     
IRIS_CD4Tcell-N0                     0    ⋯ 0      0      0      0      0     
IRIS_CD4Tcell-Th1-restimulated12hour 0    ⋯ 0      0      0      0      0     
IRIS_CD4Tcell-Th1-restimulated48hour 0    ⋯ 0      0      0      0      0     
                                     LV1038 LV1039 LV1040 LV1041 LV1042
IRIS_Bcell-Memory_IgG_IgA            0      0      0      0      0     
IRIS_Bcell-Memory_IgM                0      0      0      0      0     
IRIS_Bcell-naive                     0      0      0      0      0     
IRIS_CD4Tcell-N0                     0      0      0      0      0     
IRIS_CD4Tcell-Th1-restimulated12hour 0      0      0      0      0     
IRIS_CD4Tcell-Th1-restimulated48hour 0      0      0      0      0

In [36]:
data(majorCellTypes)
corOut=cor(t(gtex_rob_model$B[, rownames(majorCellTypes)]), majorCellTypes, method="s")
rownames(corOut)=strtrim(rownames(corOut),30)
pheatmap(corOut) + theme(text = element_text(size = 3)

ERROR: Error in parse(text = x, srcfile = src): <text>:5:0: unexpected end of input
3: rownames(corOut)=strtrim(rownames(corOut),30)
4: pheatmap(corOut) + theme(text = element_text(size = 3)
  ^


In [34]:
options(repr.plot.width=4, repr.plot.height=3)
plotU(gtex_rob_model, auc.cutoff = 0.70, fdr.cutoff = 0.05, top = 3)